In [ ]:
!pip install fitz

In [5]:
!pip install PyMuPDF

     |████████████████████████████████| 8.7 MB 7.5 MB/s 


In [6]:
import fitz
import json
import re
import nltk
from pymystem3 import Mystem
import nltk
import string
from nltk.corpus import stopwords
import pymorphy2
import concurrent.futures

In [49]:
docs_know = ['знать-1.pdf', 'знать-2.pdf']
docs_can = ['уметь-1.pdf', 'уметь-2.pdf', 'уметь-3.pdf']
docs_skill = ['владеть-1.pdf', 'владеть-2.pdf']

dict_know = {
    'знать-1.pdf': [20, 27, 39, 69, 104, 127, 164, 177, 195, 215, 226, 252, 278, 314, 332, 345],
    'знать-2.pdf': [6, 38, 93, 137, 176, 231, 278, 330, 372, 409]
}
dict_can = {
    'уметь-1.pdf': [24, 50, 80, 119, 146, 209, 269, 306, 356, 383, 388],
    'уметь-2.pdf': [25, 63, 121, 153, 199, 223, 239, 267, 291, 323, 351, 401, 453, 483, 523, 593],
    'уметь-3.pdf': [12, 28, 49, 72, 94, 125, 161, 232, 258, 295]
}
dict_skill = {
    'владеть-1.pdf': [21, 43, 61, 82, 96, 149, 199, 237, 282, 316, 355, 373, 409, 422, 443, 469, 495, 508, 530, 548, 604],
    'владеть-2.pdf': [20, 53, 83, 111, 148, 209, 253, 274, 301, 337, 347, 367, 368, 372, 382, 391, 393, 397, 400, 405]
}

documents_know = []
documents_can = []
documents_skill = []
for pdf in docs_know:
    doc = fitz.open(pdf)
    document = ""
    for i in range(doc.pageCount):
        if i in dict_know[pdf]:
            documents_know.append(document)
            document = ""
        page = doc.load_page(i)
        document += page.get_text('text')
    documents_know.append(document)

for pdf in docs_can:
    doc = fitz.open(pdf)
    document = ""
    for i in range(doc.pageCount):
        if i in dict_can[pdf]:
            documents_can.append(document)
            document = ""
        page = doc.load_page(i)
        document += page.get_text('text')
    documents_can.append(document)

for pdf in docs_skill:
    doc = fitz.open(pdf)
    document = ""
    for i in range(doc.pageCount):
        if i in dict_skill[pdf]:
            documents_skill.append(document)
            document = ""
        page = doc.load_page(i)
        document += page.get_text('text')
    documents_skill.append(document)

In [2]:
# загрузка для нс
docs_neural = ['знать-1.pdf', 'знать-2.pdf', 'уметь-1.pdf', 'уметь-2.pdf', 'уметь-3.pdf', 'владеть-1.pdf', 'владеть-2.pdf']
documents_neural = []
for pdf in docs_neural:
    doc = fitz.open(pdf)
    document = ""
    for i in range(doc.pageCount):
        page = doc.load_page(i)
        document += page.get_text('text')
    documents_neural.append(document)

In [3]:
len(documents_neural)

7

In [50]:
print(documents_can[0])
print(len(documents_know))
print(len(documents_can))
print(len(documents_skill))

ББК 32.973.2-018.1
УДК 004.43
Ш78
 
Шолле Франсуа 
Ш78 
 Глубокое обучение на Python. — СПб.: Питер, 2018. — 400 с.: ил. — (Серия «Биб-
лиотека программиста»).
 
ISBN 978-5-4461-0770-4
Глубокое обучение — Deep learning — это набор алгоритмов машинного обучения, которые мо-
делируют высокоуровневые абстракции в данных, используя архитектуры, состоящие из множества 
нелинейных преобразований. Согласитесь, эта фраза звучит угрожающе. Но всё не так страшно, 
если о глубоком обучении рассказывает Франсуа Шолле, который создал Keras — самую мощную 
библиотеку для работы с нейронными сетями. Познакомьтесь с глубоким обучением на практических 
примерах из самых разнообразных областей. Книга делится на две части: в первой даны теоретиче-
ские основы, вторая посвящена решению конкретных задач. Это позволит вам не только разобраться 
в основах DL, но и научиться использовать новые возможности на практике.
Обучение — это путешествие длиной в жизнь, особенно в области искусственного интеллекта, 
гд

In [5]:
def remove_garbage(raw_text):
  text = re.sub('\W', ' ', raw_text)
  text = re.sub('\d', ' ', text)
  text = re.sub('_', ' ', text)
  return text

print(remove_garbage('wqewr8545/,.'))

wqewr       


In [4]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\evgen\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [2]:
def to_base_form(raw_text):
  mstem = Mystem()
  tokens = mstem.lemmatize(raw_text)
  string = ''
  for elem in tokens:
    string = string + elem
  return tokens[:-1]

temp = "это мы питон."
to_base_form(temp)

['это', ' ', 'мы', ' ', 'питон', '.']

In [14]:

morph = pymorphy2.MorphAnalyzer()

def to_base_form_neural(raw_text, morph):
    text = raw_text.lower()
    result = []
    for elem in text.split(' '):        
        result.append(morph.parse(elem)[0].normal_form)
    return result

to_base_form_neural('Глубокое обучение - deep learning', morph)

['глубокий', 'обучение', '-', 'deep', 'learning']

In [12]:
nltk.download('stopwords')
stop_words = set(stopwords.words('russian'))
print(stop_words)

{'никогда', 'и', 'ей', 'эту', 'она', 'о', 'тогда', 'всего', 'этого', 'были', 'да', 'нее', 'для', 'между', 'над', 'уж', 'раз', 'я', 'ж', 'всю', 'чтобы', 'нет', 'им', 'со', 'теперь', 'когда', 'потому', 'свою', 'такой', 'более', 'эти', 'по', 'этой', 'он', 'не', 'тот', 'так', 'если', 'какая', 'ведь', 'опять', 'один', 'при', 'от', 'в', 'этот', 'мой', 'совсем', 'чуть', 'два', 'вам', 'они', 'перед', 'что', 'уже', 'всех', 'как', 'до', 'ты', 'мы', 'нельзя', 'себе', 'ему', 'за', 'сам', 'всегда', 'их', 'а', 'много', 'после', 'тем', 'этом', 'во', 'ли', 'будто', 'об', 'у', 'же', 'вдруг', 'нибудь', 'почти', 'нас', 'может', 'сейчас', 'моя', 'вас', 'к', 'потом', 'через', 'быть', 'зачем', 'под', 'была', 'тебя', 'на', 'все', 'кто', 'про', 'впрочем', 'том', 'три', 'ну', 'есть', 'лучше', 'но', 'него', 'наконец', 'или', 'чего', 'другой', 'хорошо', 'того', 'только', 'то', 'меня', 'было', 'ничего', 'чем', 'с', 'ним', 'тоже', 'вот', 'можно', 'какой', 'ни', 'из', 'вы', 'будет', 'больше', 'иногда', 'себя', 'раз

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\evgen\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [13]:
stop_words = set(stopwords.words('russian'))
punct = string.punctuation
def remove_stop_words(raw_text):
  text = [word for word in raw_text if not word in stop_words]
  return text

temp = ['это', ' ', 'мы', ' ', 'питон']
remove_stop_words(temp)

['это', ' ', ' ', 'питон']

In [56]:
def get_prepared(document):
  document_without = remove_garbage(document)
  base_document = to_base_form(document_without)
  base_document_without_stopword = remove_stop_words(base_document)
  doc_string = ''
  for e in base_document_without_stopword:
      doc_string += e
  doc_string = re.sub('\s+', ' ', doc_string)
  print('D')
  return doc_string

In [24]:
def get_prepared_for_neural(document, morph):
  doc_split = document.split('. ')
  document_prepared = []
  for sentence in doc_split:
    sentence_without = remove_garbage(sentence)
    base_sentence = to_base_form_neural(sentence_without, morph)
    base_sentence_without_stopword = remove_stop_words(base_sentence)
    sentence_string = ''
    for word in base_sentence_without_stopword:
      sentence_string += word + ' '
    sentence_string = re.sub('\s+', ' ', sentence_string)
    document_prepared.append(sentence_string)
  print('D')
  return document_prepared

In [25]:
def get_prepared_all_documents(documents):
    result = []
    for document in documents:
        result.append(get_prepared(document))
    return result

In [26]:
def get_prepared_all_documents_for_neural(documents):
    result = []
    morph = pymorphy2.MorphAnalyzer()
    for document in documents:
        result.append(get_prepared_for_neural(document, morph))
    return result

In [27]:
result_neural = get_prepared_all_documents_for_neural(documents_neural)
print(result_neural)

D
D
D
D
D
D
D
[['мама ', 'вложить сила время дать хороший образование тара ', 'ия надеяться книга увидеть свой вклад папа ', 'спасибо любить сильно найти время обучить программирование технология ещё очень юный возраст ', 'добиться это честь ваш сын grokking deep learning andrew w ', 'trask ii manning sh el t er is l an d рокать глубокий обучение эндрю траск пптереть санкт петербург москва екатеринбург воронеж нижний новгород ростов дон самара минск эндрю траск грохать глубокий обучение серия библиотека программист перевести английский ', 'киселёв заведовать редакция ю ', 'сергиенко ведущий редактор ', 'тульцева литературный редактор ', 'бульченко художественный редактор ', 'мостипан корректор ', 'беляев м ', 'молчанов вёрстка л ', 'егоров ббк удк траск эндрю грокать глубокий обучение ', ' спб питер ', ' ил ', ' серия библиот ка программист isbn глубокий обучение это раздел искусственный интеллект цель который научить компьютер обу чаться помощь нейронный сеть технология создать образ 

In [29]:
with open("data/texts/prepared_documents_neural.json", "w", encoding='utf-8') as write_file:
    json.dump(result_neural, write_file)

In [31]:
l = [1,2,3,4]
print(l[2:4])

[3, 4]


In [58]:
result_know = get_prepared_all_documents(documents_know)
result_can = get_prepared_all_documents(documents_can)
result_skill = get_prepared_all_documents(documents_skill)

D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D
D


In [59]:
print(range(len(result_know)))
print(range(len(result_can)))
print(range(len(result_skill)))

range(0, 28)
range(0, 40)
range(0, 43)


In [63]:
with open("prepared_documents_know_2.json", "w", encoding='utf-8') as write_file:
    json.dump(result_know, write_file)
with open("prepared_documents_can_2.json", "w", encoding='utf-8') as write_file:
    json.dump(result_can, write_file)
with open("prepared_documents_skill_2.json", "w", encoding='utf-8') as write_file:
    json.dump(result_skill, write_file)